In [66]:
import numpy as np
import pandas as pd
import os
import glob

PRÉ REQUISITOS PARA RODAR ESSE ESTUDO:


    Arquivo Estoque
    Arquivo draft
    Tabelas de pedido do ciclo atual e ciclo atual +1
    Tabela de preços (BI)
    Planilha de PDVs

In [67]:


# Caminho onde estão as subpastas com os arquivos CSV
pasta_entrada = r"C:\Users\roberto.alves\Documents\arquivos importantes\ESTUDO_BAZAR_02.04.25\ESTOQUE"

# Lista todas as subpastas dentro de "ESTOQUE"
subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

df_list = []

# Percorre todas as subpastas
for subpasta in subpastas:
    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

    for arquivo in arquivos:
        caminho_arquivo = os.path.join(subpasta, arquivo)
        try:
            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
            df_list.append(df)
        except Exception as e:
            print(f"Erro ao ler o arquivo {arquivo}: {e}")

if df_list:
    df_estoque = pd.concat(df_list, ignore_index=True)



In [73]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\roberto.alves\Documents\arquivos importantes\ESTUDO_BAZAR_02.04.25\DRAFT"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)
df_draft.shape


(113638, 46)

In [83]:
df_bi_preco = pd.read_excel(r"C:\Users\roberto.alves\Documents\arquivos importantes\ESTUDO_BAZAR_02.04.25\PREÇO BI\TABELA DE PREÇOS.xlsx")

In [78]:
df_ciclo6= pd.read_excel(r"C:\Users\roberto.alves\Documents\arquivos importantes\ESTUDO_BAZAR_02.04.25\TABELAS DE PEDIDO\Pedidos Semanais Especiais - GKD - 202506.xlsx")
df_ciclo7 = pd.read_excel(r"C:\Users\roberto.alves\Documents\arquivos importantes\ESTUDO_BAZAR_02.04.25\TABELAS DE PEDIDO\Pedidos Semanais Especiais - GKD - 202507.xlsx")

In [86]:
df_pdv = pd.read_excel(r"C:\Users\roberto.alves\GRUPO GINSENG\Assistência Suprimentos - BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\PDV\DB_PDV.xlsx")


In [68]:

df_estoque = df_estoque[~df_estoque['CATEGORIA'].isin(["SUPORTE À VENDA","EMBALAGENS"])] #excluindo apenas o que possui categoria igual a "SUPORTE À VENDA" e "EMBALAGENS"

df_estoque = df_estoque[df_estoque['ESTOQUE ATUAL']> 0.0 ]


df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

df_estoque = df_estoque[df_estoque['Arquivo_Origem'] == "EUD.csv"]



In [ ]:
df_estoque['DDV PREVISTO'] = np.where(df_estoque['DDV PREVISTO'].isna(),0.001,df_estoque['DDV PREVISTO']) # em casos de DDV(dias de venda) faltante assumir que o ddv é 0.0001 

df_estoque['PREVISAO_VENDAS_45D'] = df_estoque['DDV PREVISTO'] * 45

df_estoque['COBERTURA_CALCULADA'] = df_estoque['ESTOQUE ATUAL'] / df_estoque['DDV PREVISTO']

df_estoque['COBERTURA_CALCULADA'] = np.where(df_estoque['COBERTURA_CALCULADA']> 1000 ,1000 ,df_estoque['COBERTURA_CALCULADA'])

df_estoque = df_estoque.reset_index()

In [ ]:
estoque_grouped = df_estoque.groupby(['PDV','DESCRICAO','SKU_FINAL','CATEGORIA','CLASSE']).agg({
    'ESTOQUE ATUAL': 'sum',
    'PREVISAO_VENDAS_45D': 'max',
    'COBERTURA_CALCULADA' : 'mean'
}).reset_index()


In [75]:
df_draft['Projeção Próximo Ciclo + 1'] = df_draft['Projeção Próximo Ciclo + 1'] - df_draft['Projeção Próximo Ciclo']

In [76]:
df_draft["PDV"]= df_draft["PDV"].astype(int)
df_draft["SKU"]= df_draft["SKU"].astype(int)

In [77]:
df_draft[['PDV','SKU','Projeção Próximo Ciclo','Projeção Próximo Ciclo + 1']].head()

PDV    SKU  Projeção Próximo Ciclo  Projeção Próximo Ciclo + 1
0  23701  49014                       7                           1
1  23702  49014                       7                           1
2  23705  49014                       2                           0
3  23706  49014                       3                           0
4  23703  49014                       6                           3

In [79]:
print(df_ciclo6.shape)
print(df_ciclo7.shape)

(3966, 23)
(2082, 23)


In [80]:
df_ciclo6 = df_ciclo6[df_ciclo6['Região']=='NNE'] #filtrando apenas região NNE
df_ciclo7 = df_ciclo7[df_ciclo7['Região']=='NNE'] #filtrando apenas região NNE

print(df_ciclo6.shape)
print(df_ciclo7.shape)

(1322, 23)
(694, 23)


In [81]:
df_ciclo6 = df_ciclo6.rename(columns= {'Ação consumidor':'Ação consumidor_Ciclo6'})
df_ciclo7 = df_ciclo7.rename(columns= {'Ação consumidor':'Ação consumidor_Ciclo7'})

df_ciclo6 = df_ciclo6.rename(columns= {'Percentual de desconto consumidor':'Percentual de desconto consumidor_Ciclo6'})
df_ciclo7 = df_ciclo7.rename(columns= {'Percentual de desconto consumidor':'Percentual de desconto consumidor_Ciclo7'})

df_ciclo6 = df_ciclo6.rename(columns= {'Ação revendedor':'Ação revendedor_Ciclo6'})
df_ciclo7 = df_ciclo7.rename(columns= {'Ação revendedor':'Ação revendedor_Ciclo7'})

df_ciclo6 = df_ciclo6.rename(columns= {'Percentual de desconto revendedor':'Percentual de desconto revendedor_Ciclo6'})
df_ciclo7 = df_ciclo7.rename(columns= {'Percentual de desconto revendedor':'Percentual de desconto revendedor_Ciclo7'})


In [82]:
df_ciclo6['Percentual de desconto consumidor_Ciclo6'].value_counts()

df_ciclo6['percent_desconto0_6'] = np.where(df_ciclo6['Percentual de desconto consumidor_Ciclo6'] != 0 ,df_ciclo6['Percentual de desconto revendedor_Ciclo6'] ,df_ciclo6['Percentual de desconto consumidor_Ciclo6'])

df_ciclo7['percent_desconto0_7'] = np.where(df_ciclo7['Percentual de desconto consumidor_Ciclo7'] != 0 ,df_ciclo7['Percentual de desconto revendedor_Ciclo7'] ,df_ciclo7['Percentual de desconto consumidor_Ciclo7'])


df_ciclo7['percent_desconto0_7']

2               10,00
3               10,00
6               10,00
9               10,00
14              10,00
            ...      
2069             0,00
2071            10,00
2074             0,00
2076            10,00
2081    33,66 | 44,12
Name: percent_desconto0_7, Length: 694, dtype: object

In [84]:

df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(int) #.str.replace(r'\.0$', '', regex=True)
df_bi_preco = df_bi_preco[df_bi_preco['MARCA'] == "EUDORA"]

In [85]:
df_bi_preco.shape

(1406, 10)

In [87]:
estoque_grouped.shape

(6887, 6)

In [88]:
df_final = pd.merge(estoque_grouped,df_pdv[['PDV','UF']], left_on="PDV",right_on="PDV",how="inner")
df_final.shape

(6887, 7)

In [89]:
df_final = pd.merge(df_final,df_bi_preco[['PC','PV','SKU2','UF']], left_on=["SKU_FINAL",'UF'],right_on=["SKU2",'UF'],how="left")
df_final

PDV                                DESCRICAO SKU_FINAL  \
0      20968             AURIEN DES COL GOLD 100ml V2     52969   
1      20968            AURIEN DES COL RUBRA 100ml V3     49496   
2      20968    AURIEN LOC HID DES CPO RUBRA 200ml V3     49487   
3      20968    AURIEN LOC ILUM DES CPO GOLD 200ml V2     49485   
4      20968               CARBON DES COL SPEED 100ml     73857   
...      ...                                      ...       ...   
6882  910291      SECRETS BAS LIQ HD/GLOW COR 90 30ml     93289   
6883  910291      SECRETS BAS LIQ HD/GLOW COR 95 30ml     93498   
6884  910291  SECRETS BASE LIQ HIDRA GLOW COR 00 30ml     93274   
6885  910291               SIAGE COND GLOW EXPT 200ml     47176   
6886  910291            SIAGE COND HAIR PLASTIA 200ml     93047   

      ESTOQUE ATUAL  PREVISAO_VENDAS_45D  COBERTURA_CALCULADA  UF     PC  \
0              17.0                2.250           340.000000  SE  35.76   
1              17.0                5.400           141.666667  SE  35.76   
2               5.0                0.045          1000.000000  SE    NaN   
3               1.0                0.000          1000.000000  SE   9.97   
4               8.0                0.045          1000.000000  SE    NaN   
...             ...                  ...                  ...  ..    ...   
6882           12.0                0.045          1000.000000  AL  19.18   
6883            8.0                0.045          1000.000000  AL  19.18   
6884            1.0                0.045          1000.000000  AL  19.18   
6885            3.0                0.045          1000.000000  AL  11.59   
6886            2.0                0.045          1000.000000  AL  11.59   

          PV     SKU2  
0     184.90  52969.0  
1     184.90  49496.0  
2        NaN      NaN  
3      52.99  49485.0  
4        NaN      NaN  
...      ...      ...  
6882   82.99  93289.0  
6883   82.99  93498.0  
6884   82.99  93274.0  
6885   49.99  47176.0  
6886   49.99  93047.0  

[6887 rows x 10 columns]

In [90]:
df_final = pd.merge(df_final,df_draft[['PDV','SKU','Projeção Próximo Ciclo','Projeção Próximo Ciclo + 1']],left_on=["PDV","SKU_FINAL"],right_on=["PDV","SKU"],how="inner")
df_final

PDV                              DESCRICAO SKU_FINAL  ESTOQUE ATUAL  \
0     20968           AURIEN DES COL GOLD 100ml V2     52969           17.0   
1     20968          AURIEN DES COL RUBRA 100ml V3     49496           17.0   
2     20968  AURIEN LOC ILUM DES CPO GOLD 200ml V2     49485            1.0   
3     20968       CHIC DES ANTIT AEROSSOL 125ml V2     52885           18.0   
4     20968                   CHIC DES COL 95ml V2     49800            5.0   
...     ...                                    ...       ...            ...   
5010  22541   SOUL PO COMP FAC ULT MATE COR 95 10g     92677            4.0   
5011  22541                    VOLPE DES COL 100ml     92219            2.0   
5012  22541                VOLPE DES COL DNA 100ml     49166            6.0   
5013  22541               VOLPE DES COL NEXT 100ml     52299           10.0   
5014  22541            VOLPE DES COL TRIUMPH 100ml     56231           25.0   

      PREVISAO_VENDAS_45D  COBERTURA_CALCULADA  UF     PC      PV     SKU2  \
0                    2.25           340.000000  SE  35.76  184.90  52969.0   
1                    5.40           141.666667  SE  35.76  184.90  49496.0   
2                    0.00          1000.000000  SE   9.97   52.99  49485.0   
3                    0.00          1000.000000  SE   6.78   35.99  52885.0   
4                    2.70            83.333333  SE  23.19  119.90  49800.0   
...                   ...                  ...  ..    ...     ...      ...   
5010                 0.00          1000.000000  AL  11.62   49.99  92677.0   
5011                 9.45             9.523810  AL  34.55  154.90  92219.0   
5012                 0.45           600.000000  AL  34.55  154.90  49166.0   
5013                 6.75            66.666667  AL  34.55  154.90  52299.0   
5014                 2.25           500.000000  AL  34.55  154.90  56231.0   

        SKU  Projeção Próximo Ciclo  Projeção Próximo Ciclo + 1  
0     52969                       0                           0  
1     49496                       0                           0  
2     49485                       0                           0  
3     52885                       0                           0  
4     49800                       0                           0  
...     ...                     ...                         ...  
5010  92677                       0                           0  
5011  92219                       8                           1  
5012  49166                       0                           0  
5013  52299                       1                           6  
5014  56231                       1                           1  

[5015 rows x 13 columns]

In [91]:
df_final = pd.merge(df_final,df_ciclo6[['Código','percent_desconto0_6']],left_on="SKU_FINAL",right_on='Código',how="left")

df_final

PDV                              DESCRICAO SKU_FINAL  ESTOQUE ATUAL  \
0     20968           AURIEN DES COL GOLD 100ml V2     52969           17.0   
1     20968          AURIEN DES COL RUBRA 100ml V3     49496           17.0   
2     20968  AURIEN LOC ILUM DES CPO GOLD 200ml V2     49485            1.0   
3     20968       CHIC DES ANTIT AEROSSOL 125ml V2     52885           18.0   
4     20968                   CHIC DES COL 95ml V2     49800            5.0   
...     ...                                    ...       ...            ...   
5010  22541   SOUL PO COMP FAC ULT MATE COR 95 10g     92677            4.0   
5011  22541                    VOLPE DES COL 100ml     92219            2.0   
5012  22541                VOLPE DES COL DNA 100ml     49166            6.0   
5013  22541               VOLPE DES COL NEXT 100ml     52299           10.0   
5014  22541            VOLPE DES COL TRIUMPH 100ml     56231           25.0   

      PREVISAO_VENDAS_45D  COBERTURA_CALCULADA  UF     PC      PV     SKU2  \
0                    2.25           340.000000  SE  35.76  184.90  52969.0   
1                    5.40           141.666667  SE  35.76  184.90  49496.0   
2                    0.00          1000.000000  SE   9.97   52.99  49485.0   
3                    0.00          1000.000000  SE   6.78   35.99  52885.0   
4                    2.70            83.333333  SE  23.19  119.90  49800.0   
...                   ...                  ...  ..    ...     ...      ...   
5010                 0.00          1000.000000  AL  11.62   49.99  92677.0   
5011                 9.45             9.523810  AL  34.55  154.90  92219.0   
5012                 0.45           600.000000  AL  34.55  154.90  49166.0   
5013                 6.75            66.666667  AL  34.55  154.90  52299.0   
5014                 2.25           500.000000  AL  34.55  154.90  56231.0   

        SKU  Projeção Próximo Ciclo  Projeção Próximo Ciclo + 1   Código  \
0     52969                       0                           0  52969.0   
1     49496                       0                           0      NaN   
2     49485                       0                           0  49485.0   
3     52885                       0                           0      NaN   
4     49800                       0                           0      NaN   
...     ...                     ...                         ...      ...   
5010  92677                       0                           0  92677.0   
5011  92219                       8                           1  92219.0   
5012  49166                       0                           0      NaN   
5013  52299                       1                           6      NaN   
5014  56231                       1                           1      NaN   

     percent_desconto0_6  
0                   0,00  
1                    NaN  
2                   0,00  
3                    NaN  
4                    NaN  
...                  ...  
5010                0,00  
5011                0,00  
5012                 NaN  
5013                 NaN  
5014                 NaN  

[5015 rows x 15 columns]

In [92]:
df_final = pd.merge(df_final,df_ciclo7[['Código','percent_desconto0_7']],left_on="SKU_FINAL",right_on='Código',how="left")

df_final

PDV                              DESCRICAO SKU_FINAL  ESTOQUE ATUAL  \
0     20968           AURIEN DES COL GOLD 100ml V2     52969           17.0   
1     20968          AURIEN DES COL RUBRA 100ml V3     49496           17.0   
2     20968  AURIEN LOC ILUM DES CPO GOLD 200ml V2     49485            1.0   
3     20968       CHIC DES ANTIT AEROSSOL 125ml V2     52885           18.0   
4     20968                   CHIC DES COL 95ml V2     49800            5.0   
...     ...                                    ...       ...            ...   
5010  22541   SOUL PO COMP FAC ULT MATE COR 95 10g     92677            4.0   
5011  22541                    VOLPE DES COL 100ml     92219            2.0   
5012  22541                VOLPE DES COL DNA 100ml     49166            6.0   
5013  22541               VOLPE DES COL NEXT 100ml     52299           10.0   
5014  22541            VOLPE DES COL TRIUMPH 100ml     56231           25.0   

      PREVISAO_VENDAS_45D  COBERTURA_CALCULADA  UF     PC      PV     SKU2  \
0                    2.25           340.000000  SE  35.76  184.90  52969.0   
1                    5.40           141.666667  SE  35.76  184.90  49496.0   
2                    0.00          1000.000000  SE   9.97   52.99  49485.0   
3                    0.00          1000.000000  SE   6.78   35.99  52885.0   
4                    2.70            83.333333  SE  23.19  119.90  49800.0   
...                   ...                  ...  ..    ...     ...      ...   
5010                 0.00          1000.000000  AL  11.62   49.99  92677.0   
5011                 9.45             9.523810  AL  34.55  154.90  92219.0   
5012                 0.45           600.000000  AL  34.55  154.90  49166.0   
5013                 6.75            66.666667  AL  34.55  154.90  52299.0   
5014                 2.25           500.000000  AL  34.55  154.90  56231.0   

        SKU  Projeção Próximo Ciclo  Projeção Próximo Ciclo + 1  Código_x  \
0     52969                       0                           0   52969.0   
1     49496                       0                           0       NaN   
2     49485                       0                           0   49485.0   
3     52885                       0                           0       NaN   
4     49800                       0                           0       NaN   
...     ...                     ...                         ...       ...   
5010  92677                       0                           0   92677.0   
5011  92219                       8                           1   92219.0   
5012  49166                       0                           0       NaN   
5013  52299                       1                           6       NaN   
5014  56231                       1                           1       NaN   

     percent_desconto0_6  Código_y percent_desconto0_7  
0                   0,00   52969.0               10,00  
1                    NaN   49496.0               10,00  
2                   0,00       NaN                 NaN  
3                    NaN       NaN                 NaN  
4                    NaN   49800.0               10,00  
...                  ...       ...                 ...  
5010                0,00       NaN                 NaN  
5011                0,00   92219.0               10,00  
5012                 NaN   49166.0               10,00  
5013                 NaN   52299.0               10,00  
5014                 NaN   56231.0       10,00 | 43,25  

[5015 rows x 17 columns]

In [93]:
df_final.drop(columns=['SKU2','SKU','Código_x','Código_y'],inplace = True)

In [94]:
df_final['COBERTURA_CALCULADA'] = round(df_final['COBERTURA_CALCULADA'],0)

df_final['PREVISAO_VENDAS_45D'] = round(df_final['PREVISAO_VENDAS_45D'],0)




In [95]:
df_final.columns

Index(['PDV', 'DESCRICAO', 'SKU_FINAL', 'ESTOQUE ATUAL', 'PREVISAO_VENDAS_45D',
       'COBERTURA_CALCULADA', 'UF', 'PC', 'PV', 'Projeção Próximo Ciclo',
       'Projeção Próximo Ciclo + 1', 'percent_desconto0_6',
       'percent_desconto0_7'],
      dtype='object')

In [97]:
df_final['percent_desconto0_6'] = df_final['percent_desconto0_6'].fillna("0,00")
df_final['percent_desconto0_7'] = df_final['percent_desconto0_7'].fillna("0,00")

In [100]:
df_final = df_final.rename(columns= {'percent_desconto0_6':'% DESCONTO CICLO 06','percent_desconto0_7':'% DESCONTO CICLO 07','SKU_FINAL':'SKU'})

In [ ]:
ordem = ['UF','PDV', 'SKU', 'DESCRICAO', 'PC', 'PV', 'ESTOQUE ATUAL', 'PREVISAO_VENDAS_45D','COBERTURA_CALCULADA',  'Projeção Próximo Ciclo','Projeção Próximo Ciclo + 1', '% DESCONTO CICLO 06','% DESCONTO CICLO 07']

df_final = df_final[ordem]

In [107]:
df_final.head()

PDV    SKU                              DESCRICAO  UF     PC      PV  \
0  20968  52969           AURIEN DES COL GOLD 100ml V2  SE  35.76  184.90   
1  20968  49496          AURIEN DES COL RUBRA 100ml V3  SE  35.76  184.90   
2  20968  49485  AURIEN LOC ILUM DES CPO GOLD 200ml V2  SE   9.97   52.99   
3  20968  52885       CHIC DES ANTIT AEROSSOL 125ml V2  SE   6.78   35.99   
4  20968  49800                   CHIC DES COL 95ml V2  SE  23.19  119.90   

   ESTOQUE ATUAL  PREVISAO_VENDAS_45D  COBERTURA_CALCULADA  \
0           17.0                  2.0                340.0   
1           17.0                  5.0                142.0   
2            1.0                  0.0               1000.0   
3           18.0                  0.0               1000.0   
4            5.0                  3.0                 83.0   

   Projeção Próximo Ciclo  Projeção Próximo Ciclo + 1 % DESCONTO CICLO 06  \
0                       0                           0                0,00   
1                       0                           0                0,00   
2                       0                           0                0,00   
3                       0                           0                0,00   
4                       0                           0                0,00   

  % DESCONTO CICLO 07  
0               10,00  
1               10,00  
2                0,00  
3                0,00  
4               10,00

In [108]:
df_final.to_excel(r"C:\Users\roberto.alves\Documents\arquivos importantes\ESTUDO_BAZAR_02.04.25\bazar_eudora.xlsx",index=False)